In [1]:
from flightanalysis.data.p23 import create_p23
from flightanalysis.schedule.definition import SchedDef
from flightanalysis.schedule import Schedule, Manoeuvre
from flightdata import Flight
from flightanalysis import State, Box
from flightplotting import plotsec, plotdtw
from flightanalysis.criteria.local import Combination 
import numpy as np
np.set_printoptions(suppress=True)

from flightanalysis import Line, Loop, Spin, StallTurn, Snap
from geometry import Transformation

Parse a flight log, rotate it to the flightline and cutoff the takeoff and landing. 

In [2]:
#parse a flight, cutoff takeoff and landing
flown = State.from_flight(
    Flight.from_csv("examples/data/p23_example.csv").flying_only(), 
    Box.from_f3a_zone("examples/data/p23_box.f3a")
)[39:405]

Create a Schedule Definition using the create_p23 generator function. Use this to create a P23 Schedule and template State information. This is done at the average depth of the flown data and in the same direction.

In [3]:
wind=np.sign(flown[0].vel.x[0])
p23_def = create_p23(wind)  # wind direction used here because it makes the M go out and the fighter turn come back again, 

p23, template = p23_def.create_template(flown.pos.y.mean(), wind)

Align the template to the flight data.

In [4]:
dist, aligned = State.align(flown, template, 10)

In [5]:
from ipywidgets import widgets, interactive
import plotly.graph_objects as go

def dtwman(man):
    man=man-1
    fig = plotdtw(p23[man].get_data(aligned), p23[man].all_elements.to_list())
    display(go.FigureWidget(data=fig.data, layout=fig.layout))


widgets.interactive(dtwman, man=widgets.IntSlider(min=1, max=17, value=1, step=1))

interactive(children=(IntSlider(value=1, description='man', max=17, min=1), Output()), _dom_classes=('widget-i…

Update the schedule to match the flight

In [6]:
intended = p23.match_intention(template[0].transform ,aligned)

Correct the intended inter element parameters to make a corrected shcedule and template

In [7]:

p23_def.update_defaults(intended)
corrected, corrected_template = p23_def.create_template(flown.pos.y.mean(), wind)


The intended template just follows the roll directions used in the flight. The corrected template corrects the roll directions if they do not fit a valid option defined in the manoeuvre parameters. We want the intended template to have these corrected roll directions.

In [8]:

intended = intended.copy_directions(corrected)

intended_template = intended.create_template(Transformation(
    aligned[0].pos,
    aligned[0].att.closest_principal()
))


In [9]:
from json import dumps
from ipywidgets import widgets, interactive
from IPython.display import display, HTML
import plotly.graph_objects as go
import numpy as np
import pandas as pd





def dgstodf(dgs):
    if len(dgs) == 0:
        return pd.DataFrame()
    max_len = max([len(v) for v in dgs.values()])

    extend = lambda vals: [vals[i] if i < len(vals) else "" for i in range(max_len)]

    dgs = {k:extend(v) for k,v in dgs.items()}
    return pd.DataFrame.from_dict(dgs)


def scoreman(man, flown, intent, corr):
    man=man-1

    transform = intended[man].get_data(aligned)[0].transform
    dgs =  p23_def[man].mps.collect(intended[man])
    score = 10 - sum([sum(dg) for dg in dgs.values()])
    
    display(widgets.HTML(f"<h1>{p23[man].uid}: {score}</h1>"))

    fig=None
    
    if intent:
        fig = plotsec(
            intended[man].get_data(intended_template).relocate(transform.pos),
            fig=fig
        )

    if flown:
        fig = plotsec(intended[man].get_data(aligned), fig=fig)
    
    if corr:
        fig = plotsec(
            p23_def[man].create(transform).create_template(Transformation(
                transform.pos,
                intended[man].get_data(corrected_template)[0].att
            )), 
            fig=fig
        )

    if fig:
        display(go.FigureWidget(fig.data, fig.layout))

    display(dgstodf({k: v for k,v in dgs.items() if sum(v) > 0}))

man=widgets.IntSlider(min=1, max=17, value=1, step=1)
flown = widgets.Checkbox(True, description="Plot Flown")
intent = widgets.Checkbox(False, description="Plot Intended")
corr = widgets.Checkbox(False, description="Plot Corrected")

controls = widgets.HBox(children=[man, flown, intent, corr])
results = widgets.interactive_output(scoreman, dict(man=man, flown=flown, intent=intent, corr=corr))

widgets.VBox([
    controls,
    results
])



In [32]:
from tkinter import W
from geometry import PZ, Point, Coord, P0, Quaternion, PY
import plotly.graph_objects as go
import json
from flightplotting.traces import trace3d
import flightplotting.templates
import plotly.express as px

man = intended[1]
el = man.elements[4]

#TODO this is a faff, add manoeuvre name to the ElDef name on creation to remove two of these lines
flown_man = man.get_data(aligned) 
template_man = man.get_data(intended_template)
flown_el = el.get_data(flown_man)
judge_el = flown_el.to_judging()
template_el = el.get_data(template_man).relocate(flown_el.pos[0])


template_itrans = template_el[0].transform
judge_itrans = flown_el.judging_itrans(template_el[0].transform)  #TODO I think there is a bug in this method

judge_template = el.create_template(judge_itrans)


#TODO This next step needs to be thought about. Should a loop be round according to the
#loop plane in the judging_itrans or in the original template itrans?
centre =el.centre(judge_itrans)   # TODO also a bug in this method as it has been built around the bug in judge_itrans
if el.ke:
    loop_normal_vector = template_itrans.rotate(PZ(np.sign(el.angle)))
else:
    loop_normal_vector = template_itrans.rotate(PY(np.sign(el.angle)))

loop_coord = Coord.from_zx(centre, loop_normal_vector, flown_el.pos[0] - centre)

fig=plotsec(flown_el, nmodels=10, width=800, height=800)
plotsec(template_el, nmodels=10, fig=fig, color="red")
#plotsec(judge_template, nmodels=10, fig=fig, color="blue")
fig.add_trace(go.Scatter3d(x=centre.x, y=centre.y, z=centre.z, mode="markers"))

for ax, col in zip([loop_coord.x_axis, loop_coord.y_axis, loop_coord.z_axis], ["red", "blue", "green"]):
    axis = Point.concatenate([loop_coord.origin, loop_coord.origin + ax * el.radius])
    fig.add_trace(go.Scatter3d(x=axis.x, y=axis.y, z=axis.z, mode="lines", line=dict(color=col)  ))

fig

In [33]:


#TODO convert all this wo work on the loop coord.

radius_vector = judge_itrans.att.transform_point(flown_el.pos - centre) 

radius = abs(radius_vector)

if el.ke:
    x, y = radius_vector.x, radius_vector.y
else:
    x, y = radius_vector.x, radius_vector.z

radial_position = np.arctan2(x,y)

wvs = flown_el.att.transform_point(flown_el.vel) #world frame velocity vector should be in a loop frame
track = np.arcsin(wvs.y/abs(wvs) ) 

roll_vector = judge_el.att.transform_point(PY(1))  # world frame roll vector, should also go to the loop frame
roll_angle = np.arctan2(roll_vector.z, roll_vector.y) 


scoredf = pd.DataFrame(
    data = np.column_stack([radial_position, radius, np.degrees(track), np.degrees(roll_angle)]),
    columns = ["radial_position", "radius", "track", "roll_angle"]
)

px.scatter(scoredf, x="radial_position", y="radius", width=600, height=300).show()
px.scatter(scoredf, x="radial_position", y="track", width=600, height=300).show()
px.scatter(scoredf, x="radial_position", y="roll_angle", width=600, height=300).show()



In [ ]:

#TODO final step for a loop element is to check the amount of loop performed.